In [23]:
# Select Soundings for Chart Display
#
# This script generates a hydrographic sounding selection based on labels rendered at scale. This subset is
# further generalized using a buffer that increases in size with depth. Additionally, overplot with soundings
# addressed by reomiving soundings whose labels intersect with contours of shallower depth. The results are
# saved to a geopackage.
#
# Inputs:
#   - scale: Scale of the target chart.
#   - starting_radius: Starting radius length for display soundings.
#   - ending_radius: Ending radius length for display soundings.
#   - horiz_spacing: Horizontal spacing between sounding labels (default=0.75mm).
#   - vert_spacing: Vertical spacing between sounding labels (default=0.75mm).
#
# Outputs:
#   - output_path: GeoPackage containing the selected soundings.
#
# Method:
#   - sounding_selection()
#
# Reference:
#   - https://github.com/NoelDyer/Sounding-Selection

# Append modules to sys path
import sys
sys.path.insert(1, r'./lib')

# Import libraries
import os
import datetime
import geopandas
from shapely.geometry import Point as shapely_point
from shapely.geometry import shape
from shapely.ops import unary_union 
from math import ceil
from utilities import *
from cartographic_model import get_carto_symbol
from reader import Reader
from tree import Tree
import json

# Define the JSON file path
PARAMS_FILE = "./input/user_parameters.json"

def load_parameters():
    """Loads parameters from the JSON file."""
    if os.path.exists(PARAMS_FILE):
        with open(PARAMS_FILE, "r") as f:
            return json.load(f)
    return {}

# Load the parameters
parameters = load_parameters()

# Extracting the parameters
input_bathymetry_path = r'./output/Bathymetric_Features/source_soundings_final.gpkg'
input_countours_path = r'./output/Bathymetric_Features/Depth_Contours.gpkg'
input_land_area_path = r'./output/Land_Features/Land_Area.geojson'
output_path = r'./output/Bathymetric_Features'
scale = parameters["scale"]
start_radius = parameters["start_radius"]
end_radius = parameters["end_radius"]
horiz_spacing = 0.75
vert_spacing = 0.75


# Depth direction, positive or negative down. This allows us to filter out intertidal and land soundings.
# This needs to be an input parameter from the user.
depth_direction = 'NEGATIVE_DOWN' # or POSITIVE_DOWN

# Read points into pointset 
# Start timing
start_time = datetime.datetime.now()
print(f"Reading Source Soundings File: {start_time}")

projected_source_data_frame = geopandas.read_file(input_bathymetry_path)
projected_coord_system = projected_source_data_frame.crs

# Filter selectable soundings to water only (not intertidal)
if depth_direction == 'NEGATIVE_DOWN':
    source = [[point.x, point.y, abs(depth)] for point, depth in zip(projected_source_data_frame.geometry, projected_source_data_frame['SOUNDG']) if depth < 0]
elif depth_direction == 'POSITIVE_DOWN':
    source = [[point.x, point.y, abs(depth)] for point, depth in zip(projected_source_data_frame.geometry, projected_source_data_frame['SOUNDG']) if depth > 0]
    
source_pointset = Reader.read_xyz_list_to_pointset(source)

# End timing
end_time = datetime.datetime.now()
elapsed_time = end_time - start_time
print(f"Reading Source Soundings File completed in {elapsed_time.total_seconds()} seconds")
print(f"Input Sounding Count: {source_pointset.get_vertices_num()}")

# Build PR-Quadtree for input soundings
# Start timing
start_time = datetime.datetime.now()
print(f"Building PR-Quadtree for Source Soundings: {start_time}")

source_capacity = int(ceil(source_pointset.get_vertices_num() * 0.0004))
source_tree = Tree(source_capacity)
source_tree.build_point_tree(source_pointset)

# End timing
end_time = datetime.datetime.now()
elapsed_time = end_time - start_time
print(f"Building PR-Quadtree completed in {elapsed_time.total_seconds()} seconds")

# Read depth contours
# Start timing
start_time = datetime.datetime.now()
print(f"Reading, Projecting, and Merging Depth Contours: {start_time}")

contours = geopandas.read_file(input_countours_path)
contours_proj = contours.to_crs(projected_coord_system) # assumes same as bathymetry
contours_proj_geoms = contours_proj.geometry.values
contours_proj_geoms_dissolve = unary_union(contours_proj_geoms)

# End timing
end_time = datetime.datetime.now()
elapsed_time = end_time - start_time
print(f"Reading Depth Contours completed in {elapsed_time.total_seconds()} seconds")

# Read land areas
# Start timing
start_time = datetime.datetime.now()
print(f"Reading, Projecting, and Merging Land Areas: {start_time}")

land_area = geopandas.read_file(input_land_area_path)
land_area_proj = land_area.to_crs(projected_coord_system) # assumes same as bathymetry
land_area_proj_geoms = land_area_proj.geometry.values
land_area_proj_dissolve = unary_union(land_area_proj_geoms)

# End timing
end_time = datetime.datetime.now()
elapsed_time = end_time - start_time
print(f"Reading Depth Contours completed in {elapsed_time.total_seconds()} seconds")

# Cartographic model analysis (hydrographic sounding selection)
if horiz_spacing == 0.75:
    print(f'Horizontal Character Spacing Set to Default 0.75 mm')
else:
    print(f'Horizontal Character Spacing Set to {horiz_spacing} mm')

if vert_spacing == 0.75:
    print(f'Vertical Character Spacing Set to Default 0.75 mm')
else:
    print(f'Vertical Character Spacing Set to {vert_spacing} mm')

# Sort list of source/chart soundings from low to high
source_soundings_sorted = sorted(source_pointset.get_all_vertices(), key=lambda k: k.get_c(2))

# list to store hydrographic selection
hydro_soundings = list()

# Label-based generalization
# Start timing
start_time = datetime.datetime.now()
print(f"Performing Hydrographic Sounding Selection: {start_time}")

while len(source_soundings_sorted) > 0:
    delete_list = list()
    source_tree.generalization(source_tree.get_root(), 0, source_pointset.get_domain(), source_soundings_sorted[0],
                               source_pointset, delete_list, 'DCM', scale, horiz_spacing, vert_spacing)

    # Delete generalized soundings from sorted vertex list
    for i in delete_list:
        delete_idx = modified_binary_search(source_soundings_sorted, i)  # Binary search increases performance
        del source_soundings_sorted[delete_idx]

    # Add to selection
    hydro_soundings.append(source_soundings_sorted[0])

    # delete current vertex from iteration
    del source_soundings_sorted[0]

# End timing
end_time = datetime.datetime.now()
elapsed_time = end_time - start_time
print(f"Performing Hydrographic Sounding Selection completed in {elapsed_time.total_seconds()} seconds")
print(f"Hydrographic Sounding Selection Count: {len(hydro_soundings)}")

# Sort hydrographic selection shallow to deep
potential_display_sorted = sorted(hydro_soundings, key=lambda k: k.get_c(2))
potential_display_count = len(potential_display_sorted)

# Create lookup list for radius length
radius_lengths = [float(start_radius) + x * (float(end_radius) - float(start_radius)) /
                  potential_display_count for x in range(potential_display_count)]
radius_dict = dict()
for i in range(potential_display_count):
    radius_dict[potential_display_sorted[i].__str__()] = radius_lengths[i]

# Build point set for radius-based generalization
potential_display_point_set = Reader.read_vertex_list_to_pointset(potential_display_sorted)
potential_display_capacity = int(ceil(potential_display_point_set.get_vertices_num() * 0.0004))
potential_display_tree = Tree(potential_display_capacity)
potential_display_tree.build_point_tree(potential_display_point_set)

# Radius-based generalization
# Start timing
start_time = datetime.datetime.now()
print(f"Selecting Display Soundings: {start_time}")

display_soundings = list()
while len(potential_display_sorted) > 0:
    delete_list = list()
    potential_display_tree.generalization(potential_display_tree.get_root(), 0,
                                          potential_display_point_set.get_domain(), potential_display_sorted[0],
                                          potential_display_point_set, delete_list,
                                          'Radius', radius_lookup=radius_dict)

    # Delete generalized soundings from sorted vertex list
    for delete in delete_list:
        delete_idx = modified_binary_search(potential_display_sorted, delete)
        if delete_idx is not None:  # Depth precision issue where radius increases but same depth
            del potential_display_sorted[delete_idx]
    display_soundings.append(potential_display_sorted[0])
    del potential_display_sorted[0]

# End timing
end_time = datetime.datetime.now()
elapsed_time = end_time - start_time
print(f"Selecting Display Soundings completed in {elapsed_time.total_seconds()} seconds")
print(f"Initial Display Sounding Count: {len(display_soundings)}")

# Evaluate sounding and depth contour overplot
print(f"Adjusting Display Soundings for Legibility Violations with Depth Contours")
display_soundings_contour_legibility = [v for v in display_soundings if not get_carto_symbol(v, scale, horiz_spacing, vert_spacing)[1].intersects(contours_proj_geoms_dissolve)]
print(f"Sounding-Contour Legibility Violation Count: {len(display_soundings) - len(display_soundings_contour_legibility)}")
print(f"Final Display Sounding Count: {len(display_soundings_contour_legibility)}")

print(f"Adjusting Display Soundings for Legibility Violations with Land Areas")
display_soundings_contour_land_legibility = [v for v in display_soundings_contour_legibility if not get_carto_symbol(v, scale, horiz_spacing, vert_spacing)[1].intersects(land_area_proj_dissolve)]
print(f"Sounding-Land Legibility Violation Count: {len(display_soundings_contour_legibility) - len(display_soundings_contour_land_legibility)}")
if len(display_soundings_contour_legibility) - len(display_soundings_contour_land_legibility) > 0:
    print(f"Soundings Located on Land - Consider Adjusting Land Areas.")
    
print(f"Final Display Sounding Count: {len(display_soundings_contour_land_legibility)}")

# Write output files
# Hydrographic selection
print(f"Writing Output Files")
hydro_soundings_out_data = {'geometry': [shapely_point(sounding.get_c(0), sounding.get_c(1)) for sounding in hydro_soundings],
                            'SOUNDG': [sounding.get_c(2) for sounding in hydro_soundings]}
hydro_soundings_data_frame = geopandas.GeoDataFrame(hydro_soundings_out_data, crs=projected_coord_system)
output_file = os.path.join(output_path, 'Hydro_Soundings.gpkg')
if os.path.exists(output_file):
    os.remove(output_file)
hydro_soundings_data_frame.to_file(output_file, layer='points_layer', driver='GPKG')

# Display soundings
display_soundings_out_data = {'geometry': [shapely_point(sounding.get_c(0), sounding.get_c(1)) for sounding in display_soundings_contour_land_legibility],
                            'SOUNDG': [sounding.get_c(2) for sounding in display_soundings_contour_land_legibility]}
display_soundings_data_frame = geopandas.GeoDataFrame(display_soundings_out_data, crs=projected_coord_system)
output_file = os.path.join(output_path, 'Display_Soundings.gpkg')
if os.path.exists(output_file):
    os.remove(output_file)
display_soundings_data_frame.to_file(output_file, layer='points_layer', driver='GPKG')

print(f"Sounding Selection Complete")

Reading Source Soundings File: 2025-04-17 09:46:58.591331
Start read_xyz_list_to_pointset
Reading Source Soundings File completed in 1.362647 seconds
Input Sounding Count: 31134
Building PR-Quadtree for Source Soundings: 2025-04-17 09:46:59.954085
Building PR-Quadtree completed in 1.733413 seconds
Reading, Projecting, and Merging Depth Contours: 2025-04-17 09:47:01.687711
Reading Depth Contours completed in 0.040163 seconds
Reading, Projecting, and Merging Land Areas: 2025-04-17 09:47:01.727940
Reading Depth Contours completed in 0.01227 seconds
Horizontal Character Spacing Set to Default 0.75 mm
Vertical Character Spacing Set to Default 0.75 mm
Performing Hydrographic Sounding Selection: 2025-04-17 09:47:01.746318
Performing Hydrographic Sounding Selection completed in 5.295331 seconds
Hydrographic Sounding Selection Count: 170
Selecting Display Soundings: 2025-04-17 09:47:07.049406
Selecting Display Soundings completed in 0.122955 seconds
Initial Display Sounding Count: 102
Adjusting

In [26]:
import geopandas as gpd
import pandas as pd

# Define file paths
depth_areas_path = './output/Bathymetric_Features/Depth_Areas.gpkg'
survey_contours_path = './output/Bathymetric_Features/Depth_Contours.gpkg'

# Load Depth Areas
depth_areas_gdf = gpd.read_file(depth_areas_path)

# Load Survey Contours
survey_contours_gdf = gpd.read_file(survey_contours_path)

# Extract unique depth values from Depth Areas
depth_areas_values = depth_areas_gdf[['DRVAL1', 'DRVAL2']].drop_duplicates().sort_values(['DRVAL1', 'DRVAL2'])
print("Depth Areas Columns:")
print(depth_areas_values)
print()
# Extract unique depth values from Survey Contours
survey_contours_values = survey_contours_gdf[['VALDCO']].drop_duplicates().sort_values('VALDCO')

# Display Depth Values using ace_tools
print("Survey Contours Columns:")
print(survey_contours_values)


Depth Areas Columns:
  DRVAL1 DRVAL2
4      0      0
1      0     10
0     10     20

Survey Contours Columns:
   VALDCO
1       0
0      10


In [29]:
import folium
import geopandas as gpd
from folium.plugins import FeatureGroupSubGroup
from IPython.display import display
import rasterio
import numpy as np  # Import NumPy
import matplotlib.cm as cm  # Import colormap module from Matplotlib
from folium.raster_layers import ImageOverlay  # Import ImageOverlay
import branca.colormap as bcm

# Paths to data
hydro_soundings_path = r'./output/Bathymetric_Features/Display_Soundings.gpkg'
land_area_path = r'./output/Land_Features/Land_Area.geojson'
survey_contours_path = './output/Bathymetric_Features/Depth_Contours.gpkg'
depth_areas_path = './output/Bathymetric_Features/Depth_Areas.gpkg'

# Load data
print("Loading data files...")

land_area_gdf = gpd.read_file(land_area_path).to_crs('EPSG:4326')
print(f"Land areas loaded: {len(land_area_gdf)} features")

hydro_soundings_gdf = gpd.read_file(hydro_soundings_path).to_crs('EPSG:4326')
print(f"Hydro soundings loaded: {len(hydro_soundings_gdf)} features")

survey_contours_gdf = gpd.read_file(survey_contours_path).to_crs('EPSG:4326')
print(f"Survey contours loaded: {len(survey_contours_gdf)} features")

depth_areas_gdf = gpd.read_file(depth_areas_path).to_crs('EPSG:4326')
print(f"Depth areas loaded: {len(depth_areas_gdf)} features")

# Get map center
map_center = hydro_soundings_gdf.geometry.unary_union.centroid
hydro_map = folium.Map(location=[map_center.y, map_center.x], zoom_start=10)
print(f"Map centered at: {map_center.y}, {map_center.x}")

# Create subgroups
markers_layer = folium.FeatureGroup(name="Markers Only", show=False).add_to(hydro_map)
integer_layer = folium.FeatureGroup(name="Integer Depth").add_to(hydro_map)
decimal_layer = folium.FeatureGroup(name="Decimal of Depth < 10m").add_to(hydro_map)
land_area_layer = folium.FeatureGroup(name="Land Areas").add_to(hydro_map)
survey_contours_layer = folium.FeatureGroup(name="Survey Contours").add_to(hydro_map)
depth_areas_layer = folium.FeatureGroup(name="Depth Areas").add_to(hydro_map)

# Add markers
print("Adding soundings markers...")
for _, row in hydro_soundings_gdf.iterrows():
    folium.CircleMarker(
        location=[row.geometry.y, row.geometry.x],
        radius=3, color='blue', fill=True, fill_color='blue', fill_opacity=0.6
    ).add_to(markers_layer)

# Add integer labels to the "Integer Depth" layer
print("Adding integer depth labels...")
for _, row in hydro_soundings_gdf.iterrows():
    depth = row['SOUNDG']
    integer_part = int(depth)
    folium.Marker(
        location=[row.geometry.y, row.geometry.x],
        icon=folium.DivIcon(
            html=f"""
            <div style="
                font-size: 14px; 
                text-align: center;
                transform: translate(-50%, -50%);
            ">
                {integer_part}
            </div>
            """
        ),
    ).add_to(integer_layer)

# Add labels with decimals for "Depth < 10m" layer
print("Adding decimal depth labels for depths <10m...")
for _, row in hydro_soundings_gdf.iterrows():
    depth = row['SOUNDG']
    if depth < 10:  # Only for depths less than 10 meters
        integer_part = int(depth)
        decimal_part = str(depth).split('.')[-1][0]  # First decimal digit
        folium.Marker(
            location=[row.geometry.y, row.geometry.x],
            icon=folium.DivIcon(
                html=f"""
                <div style="
                        font-size: 10px; 
                        position: relative; 
                        left: 5px; 
                        top: 2px;
                    ">
                        {decimal_part}
                </div>
                """
            ),
        ).add_to(decimal_layer)

# Add land area polygons with ENC color
print("Adding land area polygons...")
for _, row in land_area_gdf.iterrows():
    folium.GeoJson(
        data=row.geometry,
        style_function=lambda x: {'fillColor': 'rgb(191, 190, 143)', 'color': '#000', 'fillOpacity': 1, 'weight': 1},
        popup=f"Land Area ID: {row.get('id', 'N/A')}"
    ).add_to(land_area_layer)

# Add depth areas with different colors based on depth range
print("Adding depth areas...")
for _, row in depth_areas_gdf.iterrows():
    try:
        depth_raw = row['DRVAL2']
        #print(f"🔍 Processing depth: {depth_raw}")

        # Convert to integer safely, handling non-numeric values
        depth = int(float(depth_raw)) if depth_raw not in [None, 'NULL', ''] else np.nan
    except ValueError:
        print(f"Invalid depth value: {depth_raw}, skipping...")
        depth = np.nan  # Assign NaN if conversion fails

    # Skip if depth is NaN (invalid)
    if np.isnan(depth):
        continue

    # Determine color based on depth
    color = 'rgb(120, 183, 150)' if depth <= 0 else \
            'rgb(97, 183, 255)' if depth <= 2 else \
            'rgb(130, 202, 255)' if depth <= 5 else \
            'rgb(167, 217, 251)' if depth <= 10 else \
            'rgb(201, 237, 255)'

    folium.GeoJson(
        data=row.geometry,
        style_function=lambda x, color=color: {'fillColor': color, 'color': color, 'fillOpacity': 0.5, 'weight': 1},
        popup=f"Depth Area: {depth}m"
    ).add_to(depth_areas_layer)

# Add survey contours with labels on the line
print("Adding survey contours...")
for _, row in survey_contours_gdf.iterrows():
    single_part = [geom.coords for geom in row.geometry.geoms]
    folium.PolyLine(
        locations=[(pt[1], pt[0]) for pt in single_part],
        color='rgb(118, 140, 151)', weight=1, opacity=1
    ).add_to(survey_contours_layer)

    mid_point = row.geometry.interpolate(0.5, normalized=True)
    depth_label = row.get('VALDCO', 'N/A')
    print(f"Contour at depth: {depth_label}m")

    folium.Marker(
        location=[mid_point.y, mid_point.x],
        icon=folium.DivIcon(html=f"<div style='font-size:10px; font-weight:bold; padding:2px;'>{depth_label}m</div>")
    ).add_to(survey_contours_layer)

# Fit map to land areas
print("Fitting map to land area bounds...")
hydro_map.fit_bounds([
    [land_area_gdf.total_bounds[1], land_area_gdf.total_bounds[0]], 
    [land_area_gdf.total_bounds[3], land_area_gdf.total_bounds[2]]
])

# Add LayerControl
folium.LayerControl(collapsed=False).add_to(hydro_map)
print("Map layers added successfully!")

# Display map
hydro_map


Loading data files...
Land areas loaded: 24 features
Hydro soundings loaded: 41 features
Survey contours loaded: 2 features
Depth areas loaded: 108 features
Map centered at: 61.14013685605719, -94.03175555832496
Adding soundings markers...
Adding integer depth labels...
Adding decimal depth labels for depths <10m...
Adding land area polygons...
Adding depth areas...
Adding survey contours...
Contour at depth: 10m
Contour at depth: 0m
Fitting map to land area bounds...
Map layers added successfully!
